## Data description
ICD-10 is the 10th revision of the International Statistical Classification of Diseases and Related Health Problems (ICD), a medical classification list by the World Health Organization (WHO). It contains codes for diseases, signs and symptoms, abnormal findings, complaints, social circumstances, and external causes of injury or diseases. Work on ICD-10 began in 1983, became endorsed by the Forty-third World Health Assembly in 1990, and was first used by member states in 1994.

In [6]:
import os
import json
import re
from os.path import join
import pandas as pd
import numpy as np

from string import punctuation
from nltk.stem.snowball import RussianStemmer, SnowballStemmer
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import nltk
nltk.download('punkt')
nltk.download('stopwords')
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.linear_model import LogisticRegression
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
from sklearn import metrics
from sklearn.metrics import classification_report, accuracy_score

from sklearn.model_selection import StratifiedKFold, train_test_split
from sklearn.svm import SVC
import itertools
from sklearn.metrics import confusion_matrix
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
from time import time

from sklearn.datasets import fetch_20newsgroups
from sklearn.ensemble  import RandomForestClassifier
%matplotlib inline

import glob, os
import artm
from artm import score_tracker


[nltk_data] Downloading package punkt to /home/vbulatov/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     /home/vbulatov/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [7]:
from bs4 import BeautifulSoup
from collections import Counter
import numpy as np
import pandas as pd

import lxml
import re
from tqdm import tqdm
import requests

main_link = 'https://ru.wikipedia.org'


In [46]:

from urllib.parse import unquote


def grab_all_links(soup):
    contents = soup.find("div", class_="mw-category")
    return {
        entry.text: entry.find("a").get('href')
        for entry in contents.findAll("li")
    }

def next_page(soup):
    items = soup.findAll("a")
    for item in items:
        if item.text == "Следующая страница":
            return item.get('href')
    return None

links = {}
current_url = '/wiki/Категория:Синдромы_по_алфавиту'
while current_url is not None:
    page_text = requests.get(main_link + current_url).text
    soup = BeautifulSoup(page_text, 'lxml')
    links.update(grab_all_links(soup))

    current_url = next_page(soup)
    print(unquote(str(current_url)))



/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=АЭРОФАГИЯ
Аэрофагия#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=ГАСТРОИНТЕСТИНАЛЬНАЯ+СТРОМАЛЬНАЯ+ОПУХОЛЬ
Гастроинтестинальная+стромальная+опухоль#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=ДЕФЕКТ+МЕЖПРЕДСЕРДНОЙ+ПЕРЕГОРОДКИ
Дефект+межпредсердной+перегородки#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=КИСТА+ЯИЧНИКА
Киста+яичника#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=МЕНИНГОЭНЦЕФАЛИТ
Менингоэнцефалит#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=ОРНИТОЗ
Орнитоз#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=ПОЗДНЯЯ+ДИСТОНИЯ
Поздняя+дистония#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=СЕКСУАЛЬНЫЕ+ДИСФУНКЦИИ
Сексуальные+дисфункции#mw-pages
/w/index.php?title=Категория:Синдромы_по_алфавиту&pagefrom=УДУШЬЕ+ДЫМОМ
Удушье+дымом#mw-pages
/w/index.php?title=Категория:Синдр

In [190]:
classes = []
categories = []
titles = []
texts = []
english_equivalents = []

def find_class_in_table(table):
    if not table:
        return None
    for table_row in table.findAll("tr"):
        for entry in table_row.findAll("a"):
            if entry.get("title") == "МКБ-10":
                other_value = table_row.find("td")
                return ''.join(other_value.findAll(text=True)).strip()

        
for title, link in tqdm(links.items()):
    soup = BeautifulSoup(requests.get(main_link+link).text, 'lxml')
    cl_name = None
    all_paragraphs = soup.findAll('p')
    page_text = ''.join(par.text for par in all_paragraphs)

    table = soup.findAll('table', attrs={"data-name": "Болезнь"})
    if table:
        cl_name = find_class_in_table(table[0])
    catlinks = soup.findAll('div', attrs={"id": "mw-normal-catlinks"})[0]
    catnames = [entry.text for entry in catlinks.findAll("a")[1:]]
    interwiki = soup.findAll('li', attrs={"class": "interwiki-en"})
    if interwiki:
        english_equivalents.append(interwiki[0].findAll("a")[0].get("href"))
    else:
        english_equivalents.append(None)

        
    classes.append(cl_name)
    titles.append(title)
    texts.append(page_text)
    categories.append(catnames)


100%|██████████| 2036/2036 [24:49<00:00,  1.37it/s]


In [191]:
df = pd.DataFrame({'class':classes, 'title':titles, 'text':texts, "english": english_equivalents, "categories": categories})

In [192]:
df['class_letter'] = df['class'].str[:1]

In [193]:
cnts = df.class_letter.value_counts()
bad_letters = cnts[cnts < 5].index

In [194]:
df.query('class_letter in @bad_letters')

class  \
345                                              Y9595.   
589                                                 W57   
591   Проявление дермографизма в виде кода медицинск...   
612                                  †E1010., F50.250.2   
626   В некоторых странах относят к K6363. («другие ...   
670                                           М40 - М54   
1269                               Xxx.x{{{2}}}{{{2}}}.   
1398                                             Z3333.   
1452                                         А81.281.2.   
1479                                    Код F (Класс V)   
1491                                                W57   
1603  .mw-parser-output .ts-comment-commentedText{bo...   
1671                                          xxx.xxx.x   
1808                                       W57, X21-X25   

                                                  title  \
345                           Внутрибольничные инфекции   
589                                      Дерматофилиазы   
591                                        Дермографизм   
612                                          Диабулимия   
626                                        Дисбактериоз   
670                                          Дорсопатия   
1269                        Падение (несчастный случай)   
1398                          Подростковая беременность   
1452  Прогрессирующая мультифокальная лейкоэнцефалоп...   
1479                           Психическое расстройство   
1491                                            Пуликоз   
1603                       Сенестопатическая шизофрения   
1671                               Синдром Смит-Магенис   
1808                                Укусы членистоногих   

                                                   text  \
345   Внутрибольничные инфекции (также госпитальные,...   
589   Дерматофилиазы (лат. Dermatophiliases) — энтом...   
591   Дермографи́зм (от др.-греч. δέρμα — кожа, γράφ...   
612   Диабулими́я (сочетанное заболевание диабета и ...   
626   Дисбактерио́з (также дисбио́з) (от др.-греч. δ...   
670   Дорсопатия (лат. dorsum «спина» + др.-греч. πά...   
1269  Паде́ние — «непреднамеренный приход в состояни...   
1398  Подростко́вая бере́менность подразумевает бере...   
1452  Прогрессивная мультифокальная лейкоэнцефалопат...   
1479  Психи́ческое расстро́йство (мента́льное расстр...   
1491  Пуликоз (лат. pulicosis) — энтомоз, поражение ...   
1603  Сенестопати́ческая шизофрени́я (от coenästheti...   
1671  Синдром Смит-Магенис (СМС) — наследственное за...   
1808  Укусы членистоногих — нападение членистоногих ...   

                                                english  \
345   https://en.wikipedia.org/wiki/Hospital-acquire...   
589             https://en.wikipedia.org/wiki/Pulicosis   
591   https://en.wikipedia.org/wiki/Dermatographic_u...   
612            https://en.wikipedia.org/wiki/Diabulimia   
626                                                None   
670            https://en.wikipedia.org/wiki/Dorsopathy   
1269   https://en.wikipedia.org/wiki/Falling_(accident)   
1398    https://en.wikipedia.org/wiki/Teenage_pregnancy   
1452  https://en.wikipedia.org/wiki/Progressive_mult...   
1479      https://en.wikipedia.org/wiki/Mental_disorder   
1491                                               None   
1603                                               None   
1671  https://en.wikipedia.org/wiki/Smith%E2%80%93Ma...   
1808  https://en.wikipedia.org/wiki/Arthropod_bites_...   

                                             categories class_letter  
345    [Синдромы по алфавиту, Инфекционные заболевания]            Y  
589                    [Синдромы по алфавиту, Энтомозы]            W  
591                [Синдромы по алфавиту, Дерматология]            П  
612   [Синдромы по алфавиту, Психотические расстройс...            †  
626           [Синдромы по алфавиту, Гастроэнтерология]            В  
670                              [Синдромы по алфавиту]            М  
1269  [Си

In [200]:
def set_fixed_class(df, title, fixed):
    idx = df.query("title == @title").index.values[0]
    df.loc[idx, 'class'] = fixed

In [202]:
set_fixed_class(df, "Дермографизм", 'L50.3')
set_fixed_class(df, "Диабулимия", 'F50.2')
set_fixed_class(df, "Дисбактериоз", 'K63')

set_fixed_class(df, "Падение (несчастный случай)", 'W00-W19')
set_fixed_class(df, "Психическое расстройство", 'F')

set_fixed_class(df, "Сенестопатическая шизофрения", 'F20.8')
set_fixed_class(df, "Синдром Смит-Магенис", 'Q93.5')
set_fixed_class(df, 'Прогрессирующая мультифокальная лейкоэнцефалопатия', 'А81.281.2')



In [205]:
df.title = df.title.str.replace(" ", "_")

In [203]:
df.to_pickle("MKB10.pkl")

In [3]:
import pandas as pd
df = pd.read_pickle("MKB10.pkl")


In [8]:

specSymb = {"«", "»", "—", "“", "-", "№"}
specSymb =  punctuation + "«»—“-№"
pattern = re.compile("[" + re.escape(specSymb) + "]")

In [9]:
from clustering_system.handler.tasks import (
    RU_DICT, KEY_MAP, LM_MODEL
)

from clustering_system.preprocessing.preprocessing_models import (
    MainModelPreprocessor
)

from clustering_system.preprocessing.dataset_collector import (
    ClientRepliesExtractor
)


preprocesser = MainModelPreprocessor(
                 ru_dictionary_path=RU_DICT, keyboard_map_path=KEY_MAP,
                 lm_model=LM_MODEL, n_jobs=8, verbose=True, log=None
         )


/home/vbulatov/miniconda3/envs/py36/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/vbulatov/miniconda3/envs/py36/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


JamSpell inited!


In [10]:
import unicodedata

def remove_accents(input_str):
    nfkd_form = unicodedata.normalize('NFKD', input_str)
    return u"".join([c for c in nfkd_form if not unicodedata.combining(c)])


def preprocess(text):
    text = text.lower()
    text = re.sub(pattern, '', text)
    text = remove_accents(text)
    return text

In [ ]:

df2 = df.copy()
df2['is_client'] = 1

# df2 = df.text
df2.index.rename("session_id", inplace=True)
df2.text = df2["text"].apply(preprocess)
df3 = df2[["text", "is_client"]].reset_index()

data_df = preprocesser.fit_transform(df3)



Start of pipeline
**************************************************************************

Start of replacer fit transform
    Start of pipeline
    **********************************************************************

    Start of html_tag_replacer fit transform
    End of html_tag_replacer fit transform
    Total time: 1.213378667831421
    ------------------------------------------------------------------
    Start of symbol_replacer fit transform
    End of symbol_replacer fit transform
    Total time: 0.011617422103881836
    ------------------------------------------------------------------
    Start of regions_tag_replacer fit transform
    End of regions_tag_replacer fit transform
    Total time: 11.2960844039917
    ------------------------------------------------------------------
    Start of towns_tag_replacer fit transform
    End of towns_tag_replacer fit transform
    Total time: 151.59716939926147
    ----------------------------------------------------------------

In [230]:
data_df

session_id                                               text  \
0              0  бедная симптомами шизофрения  подтип шизотипич...   
1              1  46xx46xy тетрагаметныи химеризм  это разновидн...   
2              2  синдром 48 xxxy  это генетическое состояние об...   
3              3  синдром 48 xxyy  это аномалия хромосом при кот...   
4              4  синдром 48 xyyy  чрезвычаино редкая анеуплоидн...   
5              5  синдром 49 xxxxy  чрезвычаино редкая анеуплоид...   
6              6  синдром 49 xxxyy  чрезвычаино редкая анеуплоид...   
7              7  синдром 49 xyyyy  чрезвычаино редкая анеуплоид...   
8              8  аббревиатоз abbreviatosis  гельминтоз из групп...   
9              9  абсанс фр absence буквально  отсутствие истори...   
10            10  абсцесс лат abscessus  нарыв  гноиное воспален...   
11            11  абсцесс головного мозга  очаговое скопление гн...   
12            12  абсцесс зуба  инфекционныи процесс которыи обу...   
13            13  абсцесс легкого абсцедирующая пневмония это гн...   
14            14  авитаминоз  заболевание являющееся следствием ...   
15            15  синдром автопивоварни также синдром ферментаци...   
16            16  агалактия от греч а без не и галактос молоко  ...   
17            17  агенезия мозолистого тела амт  редкии врожденн...   
18            18  агорафобия от дргреч αγορα базар рынок  φοβος ...   
19            19  агранулоцитоз представляет собои патологическо...   
20            20  аддисоническии криз гипоадреналовыи криз остра...   
21            21  аденовирусная инфекция  группа инфекционных за...   
22            22  аденокарцинoма дргреч αδην  железа и дргреч κα...   
23            23  аденома лат adenoma от дргреч αδην железа  ομα...   
24            24  аденомы гипофиза  опухоли железистои ткани гип...   
25            25  аденома надпочечника  собирательное понятие до...   
26            26  аденома паращитовиднои железы паратиреоаденома...   
27            27  аденома сальных желез  доброкачественная опухо...   
28            28  аденома щитовиднои железы лат adenoma glandula...   
29            29  аденоматозные полипы или аденомы  это истинные...   
...          ...                                                ...   
2006        2006  язва роговицы  или  язвенныи кератит    воспал...   
2007        2007  язвенныи колит или неспецифическии язвенныи ко...   
2008        2008  японскии энцефалит летнеосеннии комариныи энце...   
2009        2009  ячмень hordeolum  острое гноиное воспаление во...   
2010        2010  ящур  острое вирусное заболевание из группы зо...   
2011        2011  birdshot хориоретинопатия  является редкои фор...   
2012        2012  cadasil  от англ cerebral autosomal dominant a...   
2013        2013  carcinoma in situ лат carcinoma in situ  рак н...   
2014        2014  gm1ганглиозидозы  редкие наследственные заболе...   
2015        2015  gm2ганглиозидоз  тяжелое наследственное заболе...   
2016        2016  gm2 ганглиозидоз вариант аб англ gm2gangliosid...   
2017        2017  синдром gracile  очень редкое аутосомнорецесси...   
2018        2018  вальгусная деформация первого пальца стопы hal...   
2019        2019  hdrсиндром англ barakat syndrome  аутосомнодом...   
2020        2020  hellpсиндром  редкое опасное осложнение в акуш...   
2021        2021  iклеточная болезнь муколипидоз ii1  наследстве...   
2022        2022  болезнь берже iga  нефропатия идиопатическая в...   
2023        2023  larva migrans лат  гельминтоз обусловленныи ми...   
2024        2024  сахарныи диабет взрослого типа у молодых диабе...   
2025        2025  morgellons англоязычные синонимы morgellons di...   
2026        2026  myriapodiasis  редкая патология связанная со с...   
2027        2027  ornithonyssosis птичии клещевои дерматит  акар...   
2028        2028  синдром pfapa лихорадки афтозного стоматита фа...   
2029        2029  у мужчин pois англ postorgasmic illness syndro...   
2030        2030  rhinonyssoid

## Load data

In [239]:
dataset_df = pd.DataFrame(
    index=df.title,
    columns=["raw_text", "vw_text"]
)
dataset_df["raw_text"] = texts
dataset_df["vw_text"] = (df['title']
                         + " |@text " + data_df['lemmatized']
                         + " |@ngram " + data_df['ngramms']
                         + " |@letter " + df['class_letter'].astype(str)
                        ).values


In [240]:
dataset_df.tail()

raw_text  \
title                                                                                              
Синдром_SERKAL                                 Синдром SERKAL — аутосомно-рецессивное заболев...   
VLDLR-ассоциированная_мозжечковая_гипоплазия   VLDLR-ассоциированная мозжечковая гипоплазия (...   
X-связанная_эндотелиальная_дистрофия_роговицы  X-связанная, или X-сцепленная, эндотелиальная ...   
X-связанный_ихтиоз                             X-связанный ихтиоз (X-сцепленный ихтиоз) — X-с...   
XX-дисгенезия_гонад                            XX-дисгенезия гонад — тип женского гипогонадиз...   

                                                                                         vw_text  
title                                                                                             
Синдром_SERKAL                                 Синдром_SERKAL |@text синдром serkal аутосомно...  
VLDLR-ассоциированная_мозжечковая_гипоплазия   VLDLR-ассоциированная_мозжечковая_гипоплазия |...  
X-связанная_эндотелиальная_дистрофия_роговицы  X-связанная_эндотелиальная_дистрофия_роговицы ...  
X-связанный_ихтиоз                             X-связанный_ихтиоз |@text связанный ихтиоз <pe...  
XX-дисгенезия_гонад                            XX-дисгенезия_гонад |@text xxдисгенезия гонада...

In [241]:

dataset_df.index.rename(name='id', inplace=True)

In [242]:
dataset_df.to_csv("MKB10.csv")